# L'Etape du Tour 2024
Results analysis

## Imports

In [3]:
import warnings
import polars as pl
import numpy as np
from plotly.subplots import make_subplots
from sklearn.model_selection import (
    KFold,
    train_test_split,
    cross_val_score,
    GridSearchCV,
)

from enduraw_src.utils import figures
from enduraw_src.edt import modelling

warnings.simplefilter(action="ignore", category=FutureWarning)

## Data

In [4]:
df_results_splits = pl.read_parquet(
    "/Users/qdouzery/Desktop/enduraw/data/edt-2024_results/df_results_splits.parquet"
)

## Preprocessing

In [13]:
##Compute mean and std of finish time by age
df_finish_time_age = (
    df_results_splits.group_by("age")
    .agg(
        pl.col("time_total_finish").count().alias("n_athletes"),
        (pl.col("time_total_finish") / 3600).mean().alias("time_total_finsh_h_mean"),
        (pl.col("time_total_finish") / 3600).std().alias("time_total_finsh_h_std"),
    )
    .sort("age")
    .filter(pl.col("n_athletes") > 20)
)

df_finish_time_age = df_finish_time_age.with_columns(
    (pl.col("time_total_finsh_h_mean") - pl.col("time_total_finsh_h_std")).alias(
        "time_total_finsh_h_mean_minus_std"
    ),
    (pl.col("time_total_finsh_h_mean") + pl.col("time_total_finsh_h_std")).alias(
        "time_total_finsh_h_mean_plus_std"
    ),
)

## Exploratory analysis

### Finish times

**Global**

In [14]:
fig = figures.init_figure()
fig = figures.histogram(
    fig,
    df_results_splits["time_total_finish"].to_numpy() / 3600,  # display in hours
    None,
    0,
    False,
    None,
    "gold",
    "Finish time (h)",
    "Number",
    "Finish times distribution",
    subtitle="All athletes",
    legend=False,
    xrange=[
        0.9 * (df_results_splits["time_total_finish"].min() / 3600),
        1.1 * (df_results_splits["time_total_finish"].max() / 3600),
    ],
    binsize=0.25,
)
fig.show()

**Comparison women vs. men**

In [15]:
fig = figures.init_figure()
fig = figures.histogram(
    fig,
    df_results_splits.filter(pl.col("sex") == "F")["time_total_finish"].to_numpy()
    / 3600,  # display in hours
    "percent",
    0,
    False,
    "Women",
    figures.from_color_name_to_rgb_str("powderblue", opacity=0.5),
    "Finish time (h)",
    "Percentage (%)",
    "Finish times distribution",
    subtitle="All athletes",
    legend=True,
    binsize=0.25,
)
fig = figures.histogram(
    fig,
    df_results_splits.filter(pl.col("sex") == "M")["time_total_finish"].to_numpy()
    / 3600,  # display in hours
    "percent",
    0,
    False,
    "Men",
    figures.from_color_name_to_rgb_str("navajowhite", opacity=0.5),
    "Finish time (h)",
    "Percentage (%)",
    "Finish times distribution",
    subtitle="All athletes",
    legend=True,
    xrange=[
        0.9 * (df_results_splits["time_total_finish"].min() / 3600),
        1.1 * (df_results_splits["time_total_finish"].max() / 3600),
    ],
    binsize=0.25,
)
fig.update_layout(barmode="overlay")
fig.show()

**Comparison by age**

In [16]:
fig = figures.init_figure()
fig = figures.scatter_plot(
    fig,
    df_finish_time_age["age"].to_numpy(),
    df_finish_time_age["time_total_finsh_h_mean"].to_numpy(),
    df_finish_time_age["time_total_finsh_h_std"].to_numpy(),
    "markers",
    "Mean",
    "silver",
    "Age",
    "Finish time (h)",
    "Finish time depending on age",
    subtitle="All athletes",
    marker_symbol="circle",
    marker_size=8,
)
fig = figures.scatter_plot(
    fig,
    df_finish_time_age["age"].to_numpy(),
    df_finish_time_age["time_total_finsh_h_mean_minus_std"].to_numpy(),
    None,
    "markers",
    "Mean ± Std",
    "red",
    "Age",
    "Finish time (h)",
    "Finish time depending on age",
    subtitle="All athletes",
    marker_symbol="line-ew",
)
fig = figures.scatter_plot(
    fig,
    df_finish_time_age["age"].to_numpy(),
    df_finish_time_age["time_total_finsh_h_mean_plus_std"].to_numpy(),
    None,
    "markers",
    "Mean ± Std",
    "red",
    "Age",
    "Finish time (h)",
    "Finish time depending on age",
    subtitle="All athletes",
    legend=False,
    marker_symbol="line-ew",
)
fig.show()

### Split times

**Correlations**

In [17]:
##Compute correlations between each split time (+ total finish time)
df_times_splits = df_results_splits.select(
    [
        "time_total_finish",
        "time_split_col1start",
        "time_split_col1finish",
        "time_split_col2start",
        "time_split_col2finish",
        "time_split_col3start",
        "time_split_col3finish",
        "time_split_col4start",
        "time_split_finish",
    ]
)
df_corr_matrix_times_splits = df_times_splits.corr()

##Correlations matrix
fig = figures.init_figure()
fig = figures.heatmap(
    fig,
    df_corr_matrix_times_splits.to_numpy(),
    df_corr_matrix_times_splits.columns,
    df_corr_matrix_times_splits.columns,
    "solar",
    [np.min(df_corr_matrix_times_splits.to_numpy()), 1],
    "Correlation",
    "",
    "",
    "Correlation matrix of split times",
    subtitle="All athletes",
    legend=False,
    text=df_corr_matrix_times_splits.select(pl.all().round(2)).to_numpy(),
    text_fontsize=10,
)
fig.show()

**Scatter plots**

In [19]:
list_splits_times = [
    col for col in df_times_splits.columns if col != "time_total_finish"
]
fig = make_subplots(rows=4, cols=2)
for r in range(4):
    for c in range(2):
        var = list_splits_times[r * 2 + c * 1]
        fig = figures.scatter_plot(
            fig,
            df_times_splits[var].to_numpy(),
            df_times_splits["time_total_finish"].to_numpy(),
            None,
            "markers",
            None,
            "black",
            f"{var} (s)",
            "Finish time (s)",
            "Finish times depending on split times",
            subtitle="All athletes",
            legend=False,
            marker_symbol="circle",
            marker_size=2,
            row=r + 1,
            col=c + 1,
        )
        fig.update_xaxes(showgrid=True, gridcolor="lightgrey", row=r + 1, col=c + 1)
        fig.update_yaxes(showgrid=True, gridcolor="lightgrey", row=r + 1, col=c + 1)
fig.update_layout(height=1000)
fig.show()

## Modelling

**Methodology**

1. Select variables of interest
2. Split dataset between train and test sets
3. Perform K-fold cross validation on train dataset to choose better ML model (linear regression, random forest, gradient boosting, etc.)
4. Optimize hyperparameters (if necessary) with a grid search, still on train dataset
5. Train final model on entire train dataset
6. Make predictions on test dataset
7. Analyse predictions 
8. Intrepret the model

**Discussion**

Some features engineering could be done. Ideas:

- Express split times as a percentage of the best split time
- Add informations concerning split, such as distance, average gradient, etc.

### Preprocessing

In [4]:
##Set variables and test set size
list_var_x = [
    "age",
    "bib",
    "sex_F",
    "time_split_col1start",
    "time_split_col1finish",
    "time_split_col2start",
    "time_split_col2finish",
]
var_y = "time_total_finish"
size_test = 0.1

##Split between X and y
df_x, df_y = modelling.split_xy(df_results_splits, list_var_x, var_y)

##Split between train and test sets
aux_df_x_train, df_x_test, aux_df_y_train, df_y_test = train_test_split(
    df_x,
    df_y,
    test_size=size_test,
    random_state=26,  # random state for reproducible results
)

### Choice of the model

In [7]:
##Initialize model
model_name = "lgbm"
model = modelling.init_model(model_name)

##K-fold cross validation
kf = KFold(n_splits=5, shuffle=True, random_state=26)
scores = cross_val_score(
    model,
    aux_df_x_train.to_numpy(),
    aux_df_y_train.to_numpy().ravel(),
    cv=kf,
    scoring="neg_mean_absolute_error",  # MAE
)
print(f"MAE: {-scores.mean()} ± {scores.std()}")

MAE: 1026.9469536744896 ± 10.822568942214849


### Optimization hyperparameters

In [9]:
##Set combinations of hyperparameters
param_grid = {
    "n_estimators": [100, 500, 1000, 2000],
    "learning_rate": [0.005, 0.01, 0.05, 0.1],
    "max_depth": [None, 5, 10, 20],
}

##Grid search to optimize hyperparameters
model = modelling.init_model(model_name)
kf = KFold(n_splits=3, shuffle=True, random_state=26)
grid_search = GridSearchCV(
    estimator=model,
    param_grid=param_grid,
    scoring="neg_mean_absolute_error",  # MAE
    cv=kf,
)
grid_search.fit(aux_df_x_train.to_numpy(), aux_df_y_train.to_numpy().ravel())

##Store grid search results into a dataframe
df_gridsearch_results = (
    pl.DataFrame(grid_search.cv_results_)
    .select(["mean_test_score", "std_test_score", "params"])
    .with_columns(-pl.col("mean_test_score"))
    .sort("mean_test_score")
)
print(f"Best hyperparameters: {grid_search.best_params_}")
print(f"Best score: {-grid_search.best_score_}")

Best hyperparameters: {'learning_rate': 0.01, 'max_depth': 5, 'n_estimators': 1000}
Best score: 1021.488156304461


### Final predictions

In [12]:
##Set model and its parameters
model_final = modelling.init_model("lgbm")
model_final.set_params(n_estimators=1000, learning_rate=0.01, max_depth=5)

##Fit model
model_final.fit(aux_df_x_train.to_numpy(), aux_df_y_train.to_numpy().ravel())

##Make predictions
y_pred = model_final.predict(df_x_test.to_numpy())
y_pred = modelling.postprocess_pred(y_pred)

##Compute errors
err = y_pred - df_y_test.to_numpy().ravel()
err_abs = np.abs(err)
mae = np.mean(err_abs)
print(f"MAE: {mae}")

MAE: 1046.922624877571


In [15]:
fig = figures.init_figure()
fig = figures.scatter_plot(
    fig,
    np.arange(
        df_results_splits["time_total_finish"].min(),
        df_results_splits["time_total_finish"].max() + 1,
        1,
    ),
    np.arange(
        df_results_splits["time_total_finish"].min(),
        df_results_splits["time_total_finish"].max() + 1,
        1,
    ),
    None,
    "lines",
    None,
    "red",
    "True",
    "Pred",
    "T",
    subtitle="t",
    legend=False,
    line_dash="solid",
)
fig = figures.scatter_plot(
    fig,
    df_y_test.to_numpy().ravel(),
    y_pred,
    None,
    "markers",
    None,
    "black",
    "Ground truth (s)",
    "Prediction (s)",
    "Comparison of predictions vs. ground truth",
    subtitle=f"{int(np.round(100 * size_test, 0))}% of athletes",
    legend=False,
    marker_symbol="circle",
    marker_size=2,
)
fig.show()

**Observations**

- Mean absolute error on finish time is ~17m30s (6% of winner's time, 3% of mean finisher's time)
- There are more underestimations than overestimations: athletes who start too fast could be a good reason for that
- Errors are more important for common athletes than best ones: best amateurs better know themselves

### Model interpretation

**Problems to install *SHAP* package**

-> Model interpretation not done yet


In [1]:
# ##
# explainer = shap.TreeExplainer(model_final)
# shap_values = explainer.shap_values(df_x_test.to_numpy())